### Creating class for strategy

In [10]:
import pandas as pd
import numpy as np
import tpqoa
import time as timeout
from datetime import datetime, timedelta
import PrepareData_v4 as PD
api = tpqoa.tpqoa("oanda.cfg")

class BreakOutTrade(tpqoa.tpqoa):
    def __init__(self, conf_file, instrument, timeframe, bar_length, units):
        super().__init__(conf_file)
        self.instrument = instrument
        self.timeframe = timeframe
        self.bar_length = pd.to_timedelta(bar_length)
        self.units = units
        self.open_bar = 0 # open bar price, required to open position
        self.buy_price = 0 # to remember last ask price
        self.sell_price = 0 # to remember last bid price
        self.sl_price = 0 # stop loss price, required to validate if trade is still open
        self.tp_price = 0 # take profit price, required to validate if trade is still open
    
    def prepare_data(self):
        now = datetime.utcnow()
        now = now - timedelta(microseconds = now.microsecond)
        date_now = "{}-{}-{} {}:{}:{}".format(now.year, now.month, now.day, now.hour, now.minute, now.second)
        past = now - timedelta(days = 3) # three days of data is enough
        date_past = "{}-{}-{} {}:{}:{}".format(past.year, past.month, past.day, past.hour, past.minute, past.second)
        
        # downloading data
        try:
            data = api.get_history(instrument = instrument, start = date_past, end = date_now,
                                granularity = 'M5', price = "M", localize = False)
            data = data.drop('complete', axis=1)
        # resample data to required timeframe
        #data = data.resample("5min", label="right").last().dropna().iloc[:-1]
        except:
            print('Error while downloading data, lets try again')
            timeout.sleep(2)
            pass
        
        self.data = PD.prepare_data(data) # use imported module
        self.last_bar = self.data.index[-1] # change the time details of last bar
        return self.data
    
    # on_success function runs everytime there is a tick, so we need to make sure it is efficient
    def on_success(self, time, bid, ask):
        '''Method called on each tick of price. 
        '''
        global position
        if self.ticks % 2 ==0:
            print(self.ticks, end = " ")
            print("Time: {} | Bid: {} | Ask: {}".format(time, bid, ask))

            # prepare data & define strategy
            recent_tick = pd.to_datetime(time)
            if recent_tick - self.last_bar > self.bar_length:
                self.open_bar = (bid+ask)/2 # remember mid price of the opening bar, required to open position
                self.prepare_data()
                print("New candle added to dataset")
                
            # BUY only on the break of the last high
            if bid > self.data.highs.iloc[-1] and self.open_bar < self.data.highs.iloc[-1]:
                self.buy_price = ask
                self.buy_order()
            # SELL only on the break of the last low
            elif ask < self.data.lows.iloc[-1] and self.open_bar > self.data.lows.iloc[-1]:
                self.sell_price = bid
                self.sell_order()
                
            # Check if existing position were closed on Oanda platform
            if position == 1:
                if ask < self.sl_price:
                    position = 0
                elif bid > self.tp_price:
                    position = 0
            elif position == -1:
                if bid > self.sl_price:
                    position = 0
                elif ask < self.tp_price:
                    position = 0

    def buy_order(self):
        global position # read global variable - position
        # If both indicators are equal 1 then BUY the asset
        try:
            if self.data.dls2.iloc[-1] == 1 and self.data.dhs2.iloc[-1] == 1:
                print("Possible BUY")
                if position == 0: # BUY if no existing position
                    self.sl_price = round(trader.data.lows.iloc[-1] - 0.1,1)
                    sl_distance = round(self.buy_price - self.sl_price,1)
                    cost_of_sl = sl_distance * 0.83 # Cost of 1 pips on SPX500
                    risk = self.units * 0.01 # Want to risk 1around 1% of account per trade
                    traded_units = round(risk/cost_of_sl,0) # Nr of units that can be traded
                    self.tp_price = round(self.buy_price + 3*sl_distance,1)                
                    order = self.create_order(self.instrument, traded_units,
                        sl_distance = sl_distance,
                        tp_price = self.tp_price,
                        suppress = True, ret = True)
                    position = 1
                    print("BUY {} for {} SL {} TP {}".format(traded_units, self.sell_price, self.sl_price, self.tp_price))
#                 elif position < 0: # Close short if exist and buy
#                     self.sl_price = round(trader.data.lows.iloc[-1] - 0.00005,5)
#                     sl_distance = round(self.buy_price - self.sl_price,5)
#                     self.tp_price = round(self.buy_price + 3*sl_distance,5)                
#                     order = self.create_order(self.instrument, -self.units*2,
#                         sl_distance = sl_distance,
#                         tp_price = self.tp_price,
#                         suppress = True, ret = True)
#                     position = 1 # Check if SL or TP was hit and close position
#                     print("CLOSING SHORT POSITIONS AND OPEN LONG {} for {} SL {} TP {}".format(self.units, self.sell_price, self.sl_price, self.tp_price))
        except:
            print("\nConnection error while buying the asset, let's try again")
            timeout.sleep(1)
            pass
        
    def sell_order(self):
        global position # read global variable - position
        # If both indicators are equal -1 then SELL the asset
        try:
            if self.data.dhs2.iloc[-1] == -1 and self.data.dls2.iloc[-1] == -1:
                print("Possible SELL")
                # SELL if no existing position
                if position == 0:
                    self.sl_price = round(trader.data.highs.iloc[-1] + 0.1,1)
                    sl_distance = round(self.sl_price - self.sell_price,1)
                    cost_of_sl = sl_distance * 0.83 # Cost of 1 pips on SPX500
                    risk = self.units * 0.01 # Want to risk 1around 1% of account per trade
                    traded_units = round(risk/cost_of_sl,0) # Nr of units that can be traded
                    self.tp_price = round(self.sell_price - 3*sl_distance,1)                
                    order = self.create_order(self.instrument, -traded_units,
                        sl_distance = sl_distance,
                        tp_price = self.tp_price,
                        suppress = True, ret = True)
                    position = -1
                    print("SELL {} for {} SL {} TP {}".format(traded_units, self.sell_price, self.sl_price, self.tp_price))
#                 elif position > 0:
#                     self.sl_price = round(trader.data.highs.iloc[-1] + 0.00005,5)
#                     sl_distance = round(self.sl_price - self.sell_price,6)
#                     self.tp_price = round(self.sell_price - 3*sl_distance,6)                
#                     order = self.create_order(self.instrument, -self.units*2,
#                         sl_distance = sl_distance,
#                         tp_price = self.tp_price,
#                         suppress = True, ret = True)
#                     position = -1
#                     print("CLOSING LONG POSITIONS AND OPEN SHORT {} for {} SL {} TP {}".format(self.units, self.sell_price, self.sl_price, self.tp_price))
        except:
            print("\nConnection error while Selling asset, let's try again")
            timeout.sleep(1)
            pass

In [11]:
instrument = "SPX500_USD"
timeframe = "M5"
bar_length = "5m"
position = 0

In [12]:
trader = BreakOutTrade("oanda.cfg", instrument, timeframe, bar_length, 10000)

In [13]:
trader.prepare_data()

C:\Users\Sylwia\Anaconda3\lib\site-packages\pandas\core\indexing.py:205: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


o       h       l       c  volume   highs  \
time                                                                        
2021-05-14 09:15:00+00:00  4140.7  4143.5  4140.6  4142.6     265  4143.5   
2021-05-14 09:20:00+00:00  4142.6  4143.0  4140.6  4140.7     153  4143.5   
2021-05-14 09:25:00+00:00  4140.8  4141.7  4140.7  4140.8     149  4143.5   
2021-05-14 09:30:00+00:00  4140.8  4142.5  4139.8  4140.8     160  4143.5   
2021-05-14 09:35:00+00:00  4140.5  4141.1  4139.9  4140.5     154  4143.5   
...                           ...     ...     ...     ...     ...     ...   
2021-05-17 05:05:00+00:00  4168.5  4172.2  4168.2  4172.2     381  4171.2   
2021-05-17 05:10:00+00:00  4172.2  4173.7  4171.5  4172.0     279  4171.2   
2021-05-17 05:15:00+00:00  4172.0  4173.0  4170.2  4170.5     320  4171.2   
2021-05-17 05:20:00+00:00  4170.2  4171.7  4170.2  4171.4      74  4171.2   
2021-05-17 05:20:00+00:00  4170.2  4171.7  4170.2  4171.4      74  4171.2   

                             lows  dhs1  dls1  dhs2  dls2  hour  
time                                                             
2021-05-14 09:15:00+00:00  4128.2  -1.0  -1.0   0.0   0.0     9  
2021-05-14 09:20:00+00:00  4128.2  -1.0  -1.0   0.0   0.0     9  
2021-05-14 09:25:00+00:00  4128.2  -1.0  -1.0   0.0   0.0     9  
2021-05-14 09:30:00+00:00  4128.2  -1.0  -1.0   0.0   0.0     9  
2021-05-14 09:35:00+00:00  4128.2  -1.0  -1.0   0.0   0.0     9  
...                           ...   ...   ...   ...   ...   ...  
2021-05-17 05:05:00+00:00  4161.8  -1.0  -1.0  -1.0   1.0     5  
2021-05-17 05:10:00+00:00  4161.8  -1.0  -1.0  -1.0   1.0     5  
2021-05-17 05:15:00+00:00  4161.8  -1.0  -1.0  -1.0   1.0     5  
2021-05-17 05:20:00+00:00  4161.8  -1.0  -1.0  -1.0   1.0     5  
2021-05-17 05:20:00+00:00  4161.8  -1.0  -1.0  -1.0   1.0     5  

[228 rows x 12 columns]

In [ ]:
while True:
    try:
        trader.stream_data(instrument, stop = 10000)
    except:
        print("\nError running the function, let's try again")
        timeout.sleep(3)
        pass

2 Time: 2021-05-17T05:21:32.910540971Z | Bid: 4171.3 | Ask: 4171.7
4 Time: 2021-05-17T05:21:34.394730718Z | Bid: 4171.3 | Ask: 4171.7
6 Time: 2021-05-17T05:21:35.242461791Z | Bid: 4171.3 | Ask: 4171.7
8 Time: 2021-05-17T05:21:37.232204830Z | Bid: 4171.3 | Ask: 4171.7
10 Time: 2021-05-17T05:21:46.250651719Z | Bid: 4171.8 | Ask: 4172.2
12 Time: 2021-05-17T05:21:58.208657989Z | Bid: 4171.5 | Ask: 4171.9
14 Time: 2021-05-17T05:22:00.652060595Z | Bid: 4171.6 | Ask: 4172.2
16 Time: 2021-05-17T05:22:00.983578725Z | Bid: 4171.7 | Ask: 4172.1
18 Time: 2021-05-17T05:22:10.536986456Z | Bid: 4171.5 | Ask: 4171.9
20 Time: 2021-05-17T05:22:16.850427438Z | Bid: 4171.5 | Ask: 4171.9
22 Time: 2021-05-17T05:22:23.298468969Z | Bid: 4171.4 | Ask: 4172.0
24 Time: 2021-05-17T05:22:26.661524150Z | Bid: 4171.5 | Ask: 4172.1
26 Time: 2021-05-17T05:22:30.448371326Z | Bid: 4171.8 | Ask: 4172.2
28 Time: 2021-05-17T05:22:53.804437679Z | Bid: 4171.9 | Ask: 4172.3
30 Time: 2021-05-17T05:22:59.557670681Z | Bid: 4171.

240 Time: 2021-05-17T05:30:25.131531792Z | Bid: 4171.1 | Ask: 4171.7
242 Time: 2021-05-17T05:30:26.016425457Z | Bid: 4171.1 | Ask: 4171.7
244 Time: 2021-05-17T05:30:30.347115316Z | Bid: 4170.9 | Ask: 4171.5
246 Time: 2021-05-17T05:30:30.910401712Z | Bid: 4170.9 | Ask: 4171.5
248 Time: 2021-05-17T05:30:31.782674947Z | Bid: 4171.0 | Ask: 4171.4
250 Time: 2021-05-17T05:30:38.125336021Z | Bid: 4170.5 | Ask: 4170.9
252 Time: 2021-05-17T05:30:44.035828970Z | Bid: 4170.3 | Ask: 4170.7
254 Time: 2021-05-17T05:30:45.546471566Z | Bid: 4170.3 | Ask: 4170.9
256 Time: 2021-05-17T05:30:47.257673291Z | Bid: 4170.0 | Ask: 4170.4
258 Time: 2021-05-17T05:30:49.879979590Z | Bid: 4170.3 | Ask: 4170.7
260 Time: 2021-05-17T05:31:00.924090932Z | Bid: 4170.0 | Ask: 4170.4
262 Time: 2021-05-17T05:31:05.838680999Z | Bid: 4169.6 | Ask: 4170.0
264 Time: 2021-05-17T05:31:11.283437225Z | Bid: 4169.3 | Ask: 4169.7
266 Time: 2021-05-17T05:31:12.139408228Z | Bid: 4169.5 | Ask: 4169.9
268 Time: 2021-05-17T05:31:23.4381

478 Time: 2021-05-17T05:38:39.893110428Z | Bid: 4169.7 | Ask: 4170.3
480 Time: 2021-05-17T05:38:40.301890983Z | Bid: 4169.8 | Ask: 4170.2
482 Time: 2021-05-17T05:38:41.839271794Z | Bid: 4169.8 | Ask: 4170.2
484 Time: 2021-05-17T05:38:43.677207729Z | Bid: 4170.0 | Ask: 4170.4
486 Time: 2021-05-17T05:38:47.251107333Z | Bid: 4169.7 | Ask: 4170.3
488 Time: 2021-05-17T05:38:48.127879373Z | Bid: 4169.7 | Ask: 4170.3
490 Time: 2021-05-17T05:38:49.560980172Z | Bid: 4170.0 | Ask: 4170.4
492 Time: 2021-05-17T05:39:05.172880756Z | Bid: 4170.0 | Ask: 4170.6
494 Time: 2021-05-17T05:39:06.171589761Z | Bid: 4170.2 | Ask: 4170.6
496 Time: 2021-05-17T05:39:09.145459841Z | Bid: 4170.1 | Ask: 4170.7
498 Time: 2021-05-17T05:39:10.524418701Z | Bid: 4170.1 | Ask: 4170.7
500 Time: 2021-05-17T05:39:14.391622901Z | Bid: 4170.0 | Ask: 4170.6
502 Time: 2021-05-17T05:39:18.274161392Z | Bid: 4170.2 | Ask: 4170.6
504 Time: 2021-05-17T05:39:25.501280119Z | Bid: 4170.8 | Ask: 4171.2
506 Time: 2021-05-17T05:39:32.5039

714 Time: 2021-05-17T05:45:07.532912205Z | Bid: 4170.1 | Ask: 4170.5
716 Time: 2021-05-17T05:45:14.593574316Z | Bid: 4169.6 | Ask: 4170.2
718 Time: 2021-05-17T05:45:14.863646365Z | Bid: 4169.8 | Ask: 4170.2
720 Time: 2021-05-17T05:45:16.328269944Z | Bid: 4169.5 | Ask: 4170.1
722 Time: 2021-05-17T05:45:19.033209729Z | Bid: 4169.7 | Ask: 4170.1
724 Time: 2021-05-17T05:45:22.361724709Z | Bid: 4169.5 | Ask: 4169.9
726 Time: 2021-05-17T05:45:25.521910623Z | Bid: 4169.6 | Ask: 4170.0
728 Time: 2021-05-17T05:45:36.828468509Z | Bid: 4169.6 | Ask: 4170.0
730 Time: 2021-05-17T05:45:38.373846964Z | Bid: 4169.6 | Ask: 4170.2
732 Time: 2021-05-17T05:45:39.098821098Z | Bid: 4169.5 | Ask: 4170.1
734 Time: 2021-05-17T05:45:39.948282349Z | Bid: 4169.6 | Ask: 4170.2
736 Time: 2021-05-17T05:45:40.846881484Z | Bid: 4169.5 | Ask: 4170.1
738 Time: 2021-05-17T05:45:41.878167746Z | Bid: 4169.6 | Ask: 4170.0
740 Time: 2021-05-17T05:45:43.598748065Z | Bid: 4169.6 | Ask: 4170.0
742 Time: 2021-05-17T05:45:46.7148

950 Time: 2021-05-17T05:53:11.149762132Z | Bid: 4168.8 | Ask: 4169.2
952 Time: 2021-05-17T05:53:12.212905554Z | Bid: 4169.0 | Ask: 4169.4
954 Time: 2021-05-17T05:53:13.985523845Z | Bid: 4169.0 | Ask: 4169.4
956 Time: 2021-05-17T05:53:15.198887097Z | Bid: 4168.7 | Ask: 4169.3
958 Time: 2021-05-17T05:53:17.875156337Z | Bid: 4169.0 | Ask: 4169.4
960 Time: 2021-05-17T05:53:20.055818765Z | Bid: 4169.5 | Ask: 4169.9
962 Time: 2021-05-17T05:53:36.875029417Z | Bid: 4169.7 | Ask: 4170.1
964 Time: 2021-05-17T05:53:40.982702164Z | Bid: 4170.5 | Ask: 4170.9
966 Time: 2021-05-17T05:53:43.449758702Z | Bid: 4170.0 | Ask: 4170.4
968 Time: 2021-05-17T05:53:47.500173124Z | Bid: 4170.0 | Ask: 4170.6
970 Time: 2021-05-17T05:53:48.193873113Z | Bid: 4170.0 | Ask: 4170.6
972 Time: 2021-05-17T05:53:48.613100087Z | Bid: 4170.1 | Ask: 4170.5
974 Time: 2021-05-17T05:53:51.315701279Z | Bid: 4170.1 | Ask: 4170.5
976 Time: 2021-05-17T05:53:53.409313700Z | Bid: 4170.0 | Ask: 4170.6
978 Time: 2021-05-17T05:53:54.0152

...

472 Time: 2021-05-21T15:05:06.497030971Z | Bid: 4175.7 | Ask: 4176.0
474 Time: 2021-05-21T15:05:07.675142630Z | Bid: 4176.0 | Ask: 4176.3
476 Time: 2021-05-21T15:05:11.546216498Z | Bid: 4176.4 | Ask: 4176.7
478 Time: 2021-05-21T15:05:12.388445871Z | Bid: 4176.4 | Ask: 4176.7
480 Time: 2021-05-21T15:05:13.516740824Z | Bid: 4176.2 | Ask: 4176.5
482 Time: 2021-05-21T15:05:18.597640786Z | Bid: 4176.0 | Ask: 4176.3
484 Time: 2021-05-21T15:05:18.980494599Z | Bid: 4176.0 | Ask: 4176.3
486 Time: 2021-05-21T15:05:20.297894243Z | Bid: 4176.4 | Ask: 4176.7
488 Time: 2021-05-21T15:05:21.366303591Z | Bid: 4176.3 | Ask: 4176.6
490 Time: 2021-05-21T15:05:21.661562398Z | Bid: 4176.1 | Ask: 4176.4
492 Time: 2021-05-21T15:05:23.479886202Z | Bid: 4176.3 | Ask: 4176.6
494 Time: 2021-05-21T15:05:26.471880321Z | Bid: 4176.2 | Ask: 4176.5
496 Time: 2021-05-21T15:05:27.313031482Z | Bid: 4176.2 | Ask: 4176.5
498 Time: 2021-05-21T15:05:28.415420077Z | Bid: 4175.9 | Ask: 4176.2
500 Time: 2021-05-21T15:05:29.4017

710 Time: 2021-05-21T15:09:43.498926328Z | Bid: 4178.0 | Ask: 4178.3
712 Time: 2021-05-21T15:09:45.524877210Z | Bid: 4177.6 | Ask: 4177.9
714 Time: 2021-05-21T15:09:46.017164096Z | Bid: 4177.6 | Ask: 4177.9
716 Time: 2021-05-21T15:09:52.494624958Z | Bid: 4178.0 | Ask: 4178.3
718 Time: 2021-05-21T15:09:59.222467038Z | Bid: 4177.7 | Ask: 4178.0
720 Time: 2021-05-21T15:10:01.881293431Z | Bid: 4177.5 | Ask: 4177.8
New candle added to dataset
722 Time: 2021-05-21T15:10:03.416123598Z | Bid: 4177.4 | Ask: 4177.7
724 Time: 2021-05-21T15:10:04.559459875Z | Bid: 4177.5 | Ask: 4177.8
726 Time: 2021-05-21T15:10:06.916134098Z | Bid: 4177.5 | Ask: 4177.8
728 Time: 2021-05-21T15:10:08.610929897Z | Bid: 4177.5 | Ask: 4177.8
730 Time: 2021-05-21T15:10:10.981496447Z | Bid: 4177.2 | Ask: 4177.5
732 Time: 2021-05-21T15:10:13.141113645Z | Bid: 4177.0 | Ask: 4177.3
734 Time: 2021-05-21T15:10:17.844432030Z | Bid: 4176.7 | Ask: 4177.0
736 Time: 2021-05-21T15:10:22.253674007Z | Bid: 4176.7 | Ask: 4177.0
738 Ti

948 Time: 2021-05-21T15:14:36.284138924Z | Bid: 4177.0 | Ask: 4177.3
950 Time: 2021-05-21T15:14:41.975566102Z | Bid: 4176.7 | Ask: 4177.0
952 Time: 2021-05-21T15:14:44.390132849Z | Bid: 4176.5 | Ask: 4176.8
954 Time: 2021-05-21T15:14:45.699208367Z | Bid: 4176.4 | Ask: 4176.9
956 Time: 2021-05-21T15:14:48.445381935Z | Bid: 4176.7 | Ask: 4177.0
958 Time: 2021-05-21T15:14:49.928893501Z | Bid: 4176.7 | Ask: 4177.0
960 Time: 2021-05-21T15:14:50.847067629Z | Bid: 4176.8 | Ask: 4177.1
962 Time: 2021-05-21T15:14:53.040518536Z | Bid: 4177.0 | Ask: 4177.3
964 Time: 2021-05-21T15:14:56.301783126Z | Bid: 4176.9 | Ask: 4177.2
966 Time: 2021-05-21T15:14:59.044170541Z | Bid: 4177.1 | Ask: 4177.4
968 Time: 2021-05-21T15:15:00.030286504Z | Bid: 4177.1 | Ask: 4177.4
New candle added to dataset
970 Time: 2021-05-21T15:15:01.476849772Z | Bid: 4177.1 | Ask: 4177.4
New candle added to dataset
972 Time: 2021-05-21T15:15:03.195554122Z | Bid: 4177.3 | Ask: 4177.8
974 Time: 2021-05-21T15:15:04.130199642Z | Bid:

1182 Time: 2021-05-21T15:19:44.283013782Z | Bid: 4177.3 | Ask: 4177.6
1184 Time: 2021-05-21T15:19:50.347810908Z | Bid: 4177.1 | Ask: 4177.4
1186 Time: 2021-05-21T15:19:51.950152697Z | Bid: 4177.2 | Ask: 4177.7
1188 Time: 2021-05-21T15:19:52.997676310Z | Bid: 4177.3 | Ask: 4177.8
1190 Time: 2021-05-21T15:19:55.910305000Z | Bid: 4177.4 | Ask: 4177.7
1192 Time: 2021-05-21T15:19:58.974636018Z | Bid: 4177.9 | Ask: 4178.2
1194 Time: 2021-05-21T15:20:04.760661041Z | Bid: 4177.7 | Ask: 4178.0
New candle added to dataset
1196 Time: 2021-05-21T15:20:11.014490225Z | Bid: 4177.9 | Ask: 4178.2
1198 Time: 2021-05-21T15:20:13.476482699Z | Bid: 4177.9 | Ask: 4178.2
1200 Time: 2021-05-21T15:20:24.002904159Z | Bid: 4178.4 | Ask: 4178.7
1202 Time: 2021-05-21T15:20:27.961770383Z | Bid: 4178.2 | Ask: 4178.5
1204 Time: 2021-05-21T15:20:30.874442941Z | Bid: 4178.1 | Ask: 4178.4
1206 Time: 2021-05-21T15:20:34.704863398Z | Bid: 4178.3 | Ask: 4178.6
1208 Time: 2021-05-21T15:20:35.914053353Z | Bid: 4178.4 | Ask:

1414 Time: 2021-05-21T15:27:03.918741501Z | Bid: 4173.4 | Ask: 4173.7
1416 Time: 2021-05-21T15:27:04.864255377Z | Bid: 4173.5 | Ask: 4173.8
1418 Time: 2021-05-21T15:27:05.463299268Z | Bid: 4173.9 | Ask: 4174.2
1420 Time: 2021-05-21T15:27:05.831334744Z | Bid: 4174.0 | Ask: 4174.3
1422 Time: 2021-05-21T15:27:08.612072897Z | Bid: 4174.4 | Ask: 4174.7
1424 Time: 2021-05-21T15:27:09.455613322Z | Bid: 4174.2 | Ask: 4174.5
1426 Time: 2021-05-21T15:27:10.162913938Z | Bid: 4174.1 | Ask: 4174.4
1428 Time: 2021-05-21T15:27:12.917898645Z | Bid: 4174.2 | Ask: 4174.5
1430 Time: 2021-05-21T15:27:13.423762945Z | Bid: 4174.4 | Ask: 4174.7
1432 Time: 2021-05-21T15:27:13.847342860Z | Bid: 4173.9 | Ask: 4174.2
1434 Time: 2021-05-21T15:27:15.536491664Z | Bid: 4173.4 | Ask: 4173.7
1436 Time: 2021-05-21T15:27:16.206012208Z | Bid: 4173.5 | Ask: 4173.8
1438 Time: 2021-05-21T15:27:16.705232722Z | Bid: 4173.6 | Ask: 4173.9
1440 Time: 2021-05-21T15:27:18.660545037Z | Bid: 4173.2 | Ask: 4173.5
1442 Time: 2021-05-2

## dla kazdego trejdu ustalam SL i TP na podstawie ceny

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
plt.figure(figsize=(30,15))
plt.plot(trader.data["h"]) #upper price
plt.plot(trader.data['c'], color='black',linewidth=2, markersize=12) #close prices
plt.plot(trader.data["l"]) #lower price
plt.scatter(trader.data.index, trader.data['highs'], marker = "v", color = "red")
plt.scatter(trader.data.index, trader.data['lows'], marker = "^", color = "green")
plt.show()

In [ ]:
price = 1.17822
sl_distance = round(price - trader.data.lows.iloc[-1],6)
tp_price = price + 3*sl_distance

In [ ]:
# na podstawie positionValue wiemy co zrobić z pozycją, dodać czy zamknąć wszystko
trader.create_order(instrument = trader.instrument,
                    units = 1000,
                    price = price,
                    sl_distance = sl_distance,
                    tp_price = tp_price,
                    suppress = True,
                    ret = True)

### Streamowanie strategii przez 50 ticków i na koniec zamknięcie pozycji

In [ ]:
trader.stream_data(trader.instrument, stop = 50) # trading (50 ticks)
close_order = trader.create_order(trader.instrument, units = -trader.position * trader.units, 
                                  suppress = True, ret = True) # close Final Position
trader.report_trade(close_order, "GOING NEUTRAL") # report Final Trade